# rf205_compplot
Addition and convolution: options for plotting components of composite pdfs.




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:17 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooAddPdf.h"
#include "RooChebychev.h"
#include "RooExponential.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "RooPlot.h"
using namespace RooFit;

Setup composite  pdf
--------------------------------------

Declare observable x

In [2]:
RooRealVar x("x", "x", 0, 10);

Create two Gaussian PDFs g1(x,mean1,sigma) anf g2(x,mean2,sigma) and their parameters

In [3]:
RooRealVar mean("mean", "mean of gaussians", 5);
RooRealVar sigma1("sigma1", "width of gaussians", 0.5);
RooRealVar sigma2("sigma2", "width of gaussians", 1);
RooGaussian sig1("sig1", "Signal component 1", x, mean, sigma1);
RooGaussian sig2("sig2", "Signal component 2", x, mean, sigma2);

[#0] WARNING:InputArguments -- The parameter 'sigma1' with range [-inf, inf] of the RooGaussian 'sig1' exceeds the safe range of (0, inf). Advise to limit its range.
[#0] WARNING:InputArguments -- The parameter 'sigma2' with range [-inf, inf] of the RooGaussian 'sig2' exceeds the safe range of (0, inf). Advise to limit its range.


Sum the signal components into a composite signal pdf

In [4]:
RooRealVar sig1frac("sig1frac", "fraction of component 1 in signal", 0.8, 0., 1.);
RooAddPdf sig("sig", "Signal", {sig1, sig2}, sig1frac);

Build Chebychev polynomial pdf

In [5]:
RooRealVar a0("a0", "a0", 0.5, 0., 1.);
RooRealVar a1("a1", "a1", 0.2, 0., 1.);
RooChebychev bkg1("bkg1", "Background 1", x, {a0, a1});

Build exponential pdf

In [6]:
RooRealVar alpha("alpha", "alpha", -1);
RooExponential bkg2("bkg2", "Background 2", x, alpha);

Sum the background components into a composite background pdf

In [7]:
RooRealVar bkg1frac("bkg1frac", "fraction of component 1 in background", 0.8, 0., 1.);
RooAddPdf bkg("bkg", "Total background", {bkg1, bkg2}, bkg1frac);

Sum the composite signal and background

In [8]:
RooRealVar bkgfrac("bkgfrac", "fraction of background", 0.5, 0., 1.);
RooAddPdf model("model", "g1+g2+a", {bkg, sig}, bkgfrac);

Setup basic plot with data and full pdf
------------------------------------------------------------------------------

Generate a data sample of 1000 events in x from model

In [9]:
std::unique_ptr<RooDataSet> data{model.generate(x, 1000)};

input_line_55:2:2: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
 std::unique_ptr<RooDataSet> data{model.generate(x, 1000)};
 ^


Plot data and complete PDF overlaid

In [10]:
RooPlot *xframe = x.frame(Title("Component plotting of pdf=(sig1+sig2)+(bkg1+bkg2)"));
data->plotOn(xframe);
model.plotOn(xframe);

input_line_56:3:1: error: reference to 'data' is ambiguous
data->plotOn(xframe);
^
input_line_55:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{model.generate(x, 1000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


Clone xframe for use below

In [11]:
RooPlot *xframe2 = (RooPlot *)xframe->Clone("xframe2");

input_line_58:2:14: error: use of undeclared identifier 'xframe'
 ((RooPlot *)xframe->Clone("xframe2"))
             ^
Error in <HandleInterpreterException>: Error evaluating expression ((RooPlot *)xframe->Clone("xframe2"))
Execution of your code was aborted.


Make component by object reference
--------------------------------------------------------------------

Plot single background component specified by object reference

In [12]:
model.plotOn(xframe, Components(bkg), LineColor(kRed));

input_line_59:2:50: error: cannot take the address of an rvalue of type 'EColor'
 model.plotOn(xframe, Components(bkg), LineColor(kRed));
                                                 ^~~~
Error while creating dynamic expression for:
  model.plotOn(xframe, Components(bkg), LineColor(kRed))


Plot single background component specified by object reference

In [13]:
model.plotOn(xframe, Components(bkg2), LineStyle(kDashed), LineColor(kRed));

input_line_60:2:51: error: cannot take the address of an rvalue of type 'ELineStyle'
 model.plotOn(xframe, Components(bkg2), LineStyle(kDashed), LineColor(kRed));
                                                  ^~~~~~~
Error while creating dynamic expression for:
  model.plotOn(xframe, Components(bkg2), LineStyle(kDashed), LineColor(kRed))


Plot multiple background components specified by object reference
Note that specified components may occur at any level in object tree
(e.g bkg is component of 'model' and 'sig2' is component 'sig')

In [14]:
model.plotOn(xframe, Components(bkg, sig2), LineStyle(kDotted));

input_line_61:2:56: error: cannot take the address of an rvalue of type 'ELineStyle'
 model.plotOn(xframe, Components(bkg, sig2), LineStyle(kDotted));
                                                       ^~~~~~~
Error while creating dynamic expression for:
  model.plotOn(xframe, Components(bkg, sig2), LineStyle(kDotted))


Make component by name / regexp
------------------------------------------------------------

Plot single background component specified by name

In [15]:
model.plotOn(xframe2, Components("bkg"), LineColor(kCyan));

[#0] ERROR:Plotting -- RooAddPdf::model:plotOn: frame is null


Plot multiple background components specified by name

In [16]:
model.plotOn(xframe2, Components("bkg1,sig2"), LineStyle(kDotted), LineColor(kCyan));

[#0] ERROR:Plotting -- RooAddPdf::model:plotOn: frame is null


Plot multiple background components specified by regular expression on name

In [17]:
model.plotOn(xframe2, Components("sig*"), LineStyle(kDashed), LineColor(kCyan));

[#0] ERROR:Plotting -- RooAddPdf::model:plotOn: frame is null


Plot multiple background components specified by multiple regular expressions on name

In [18]:
model.plotOn(xframe2, Components("bkg1,sig*"), LineStyle(kDashed), LineColor(kYellow), Invisible());

[#0] ERROR:Plotting -- RooAddPdf::model:plotOn: frame is null


Draw the frame on the canvas

In [19]:
TCanvas *c = new TCanvas("rf205_compplot", "rf205_compplot", 800, 400);
c->Divide(2);
c->cd(1);
gPad->SetLeftMargin(0.15);
xframe->GetYaxis()->SetTitleOffset(1.4);
xframe->Draw();
c->cd(2);
gPad->SetLeftMargin(0.15);
xframe2->GetYaxis()->SetTitleOffset(1.4);
xframe2->Draw();
c->Draw();

[runStaticInitializersOnce]: Failed to materialize symbols: { (main, { __orc_init_func.cling-module-322, _ZN12__cling_N53716__cling_Un1Qu337EPv, _GLOBAL__sub_I_cling_module_322, _ZN12__cling_N5371cE, _ZN7TObjectnwEm, $.cling-module-322.__inits.0, __cxx_global_var_initcling_module_322_ }) }
IncrementalExecutor::executeFunction: symbol '_ZN5cling7runtime8internal9EvaluateTIvEET_PNS1_15DynamicExprInfoEPN5clang11DeclContextE' unresolved while linking [cling interface function]!
You are probably missing the definition of void cling::runtime::internal::EvaluateT<void>(cling::runtime::internal::DynamicExprInfo*, clang::DeclContext*)
Maybe you need to load the corresponding shared library?
